# Train each author as classifier
1. Either apply threshold to samples in each name group so each author classifier only trained with samples pass threshold

2. Or not apply threshold to samples so each author classifier trained with all samples (include samples can't pass threshold) 

Example: k-kim name group have 1111 samples for 57 author.

With threshold of 100:

method 1 have 504 sample for training 3 author classifier.

method 2 have 1111 sample for training 3 author classifier.

In [9]:
import os
import sys
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
    
import com_func

# parameters
#----- threshold for selecting set of name group -----------#
threshold_select_name_group = 100
#----- threshold for selecting min sample in name group ----#
threshold_lower = 10
threshold_upper = 110

pp_textual = ["lsa", "pv_dm", "pv_dbow"]
apply_threshold_to_sample = True

Dataset = "pubmed"

In [10]:
def read_labeled_file(infile):
    LabeledRecords_original = []
    with open(infile, 'r', encoding = 'utf8') as f:
        for line in f:
            read_data = line.split("\t")
            # get ride of bad formated lines
            if(len(read_data)==13 or len(read_data)==12):
                paper_detail = {"paperID": read_data[0], "authorID":read_data[1]}
                LabeledRecords_original.append(paper_detail)
            else:
                print(len(read_data))
        f.close()
    return pd.DataFrame(LabeledRecords_original)

In [11]:
# remove author(positive sample) from other(negative sample)
import random
def extractNegativeSample(positiveSample, allSample):
    negativeSample = [x for x in allSample if x not in positiveSample]
    return negativeSample

In [12]:
def extract_embedding(all_embedding, all_embedding_pid, wanted_pid_list):
    extracted_emb = []
    wanted_pid_list = wanted_pid_list.values.tolist()
    total_missing_sample = 0
    # only if embedding exist
    if len(all_embedding)>0:
        # loop through wanted pid list to keep input order
        for wanted_pid in wanted_pid_list:
            # if wanted paper in all pretrained embeddings
            if wanted_pid in all_embedding_pid:
                emb_idx = all_embedding_pid.index(wanted_pid)
                extracted_emb.append(all_embedding[emb_idx])
            # if wanted paper not in all pretrained embeddings, fill missing sample with 0's
            else:
                total_missing_sample+=1
                print("Missing Sample: ", wanted_pid)
                temp = [0] * len(all_embedding[0])
                extracted_emb.append(temp)
    print("Total missing sample: ", total_missing_sample)
    extracted_emb = pd.DataFrame(extracted_emb)
    return extracted_emb

In [13]:
from sklearn import metrics
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import precision_score, recall_score,f1_score,accuracy_score
# cross validation
def k_fold_cv(data, label, clf, k=10):
    kf = StratifiedKFold(n_splits=k, shuffle=False)
    allTrueLabel = []
    allPredLabel = []
    for train_index, test_index in kf.split(data, label):
        # print("TRAIN:", train_index, " \n TEST:", test_index)
        # split train and test
        data_train, data_test = data[train_index], data[test_index]
        label_train, label_test = label[train_index], label[test_index]
        # fit data to clf
        clf.fit(data_train, label_train)
        # get predicted label
        label_pred = clf.predict(data_test)
        allTrueLabel.extend(label_test)
        allPredLabel.extend(label_pred)
        # print("True positive: {tp}, False positive: {fp}, False negative: {fn}, True negative: {tn}"
        # .format(tp=round_tp, fp=round_fp, fn=round_fn, tn=round_tn))

    accuracy = accuracy_score(allTrueLabel, allPredLabel)
    f1 = f1_score(allTrueLabel, allPredLabel,average='macro')
    
    print(metrics.classification_report(allTrueLabel, allPredLabel))
    print(metrics.confusion_matrix(allTrueLabel, allPredLabel).ravel())
    
    return accuracy, f1

In [15]:
# load the file
import sys
import io
import os
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from statistics import mean 

# fix random seed for reproducibility
np.random.seed(1)

fileDir = "../../Data/"+Dataset+"/canopies_labeled/"
listfiles = os.listdir(fileDir)

lr_diff_emb_f1_result = []
svm_diff_emb_f1_result = []


for select_emb in pp_textual:
    print("Load embedding: ", select_emb)
    # read pretrained embeddings
    emb_all_sample, emb_all_pid = com_func.read_textual_embedding(emb_type=select_emb, training_size = "3m")
    
    threshold_change_all_lr_f1s = []
    threshold_change_all_svm_f1s = []
    threshold_change = []
    
    # -------------- different threshold (step by 10) -----------------------#
    for step_threshold in range(threshold_lower, threshold_upper, 10):
        threshold_change.append(step_threshold)
        # collect statistic to output
        allname, positive_sample_size, negative_sample_size, total_sample_size= ([] for i in range(4))
        all_LR_accuracy, all_LR_f1, all_svcLinear_accuracy, all_svcLinear_f1 = ([] for i in range(4))
        
        total_selected_group = 0

        # read all file in labeled group
        for file in listfiles:
            # group name
            temp = file.split("_")
            name = temp[1]+"_"+temp[-1]
            print("For name: ",name)
            # read needed content in labeled file
            labeled_data = read_labeled_file(fileDir+file)
            # ---------------- collect all labeled sample -------------------- #
            # ---------------- if use all samples as negative --------------- #
            all_labeled_samples = labeled_data["paperID"].tolist()
            #----------- select name group contain productive author------------------------------------#
            #----------- (contain pair of author write more than 100 papers) ---------------------------#
            authorCounter = com_func.select_productive_groups(labeled_data, threshold_select_name_group)
            # if only have one class or no class pass the threshold, not applicable
            if(len(authorCounter)==0) or (len(authorCounter)==1):
                print(name, " pass")
            else:
                total_selected_group+= 1
                # --------------for each name group---------------- #
                if apply_threshold_to_sample == True:
                    # ---------- only use sample pass threshold ------- #
                    #-------- only select authors in name group are very productive (more than threshold)---------#
                    labeled_data, author_list,_= com_func.only_select_productive_authors(labeled_data, step_threshold)
                    # ----------------- if use filtered samples as negative --------- #
                    filtered_all_labeled_samples = labeled_data["paperID"].tolist()
                else:
                    # ----------- use all sample in name group --------- #
                    author_list = com_func.productive_authors_list(labeled_data, step_threshold)
                    print(name, " name group sample size: ",labeled_data.shape)
                # shuffle the data
                labeled_data = labeled_data.sample(frac=1).reset_index(drop=True)
                # list of different data field
                part_collection = []
                # select feature wanted to fit to clustering/classification algorithm
                data_textual = extract_embedding(emb_all_sample, emb_all_pid, labeled_data["paperID"])
                print(data_textual.shape)
                part_collection.append(data_textual)
                # merge different part of data data together by concatenate it all together
                combinedata = com_func.merge_data_parts(part_collection)
                print(combinedata.shape)
                # ------------- index tracker -------------------- #
                group_pid = labeled_data["paperID"].to_frame()
                counter = 0
                # loop through each author have label, one vs rest
                for author in author_list:
                    total_sample_size.append(len(labeled_data))
                    author_name = name+'_'+str(counter)
                    allname.append(author_name)
                    print(author_name, " : ", author)
                    mask = labeled_data["authorID"] == author
                    temp = labeled_data[mask]
                    positive_sample_pid = temp["paperID"].tolist()
                    negative_sample_pid = extractNegativeSample(positive_sample_pid, filtered_all_labeled_samples)
                    # append to statistic collection
                    positive_sample_size.append(len(positive_sample_pid))
                    negative_sample_size.append(len(negative_sample_pid))
                    # form positive and negative (negative class come from similar name group)
                    all_authors = []
                    all_authors.append(positive_sample_pid)
                    all_authors.append(negative_sample_pid)
                    appended_data = []
                    for label, pid in enumerate(all_authors):
                        # create df save one author data 
                        authordf = pd.DataFrame({"paperID":pid})
                        authordf['label'] = label
                        appended_data.append(authordf)
                    processed_data = pd.concat(appended_data, axis=0,ignore_index=True)

                    # alignment 
                    processed_data = pd.merge(group_pid, processed_data, on="paperID")

                    # extract true label and it's corresponeding pid for matching
                    label = processed_data["label"]
                    pid = processed_data["paperID"]

                    # using converted feature vector to train classifier
                    # using logistic regression
                    clf = LogisticRegression()
                    LRaccuracy, LRmarcof1 = k_fold_cv(combinedata, label, clf, k=10)
                    print("LR Accuracy: ",LRaccuracy)
                    print("LR F1: ", LRmarcof1)
                    all_LR_accuracy.append(LRaccuracy)
                    all_LR_f1.append(LRmarcof1)
                    # using SVM with linear kernal
                    clf = SVC(kernel='linear')
                    svcaccuracy, svcmarcof1 = k_fold_cv(combinedata, label, clf, k=10)
                    print("svc Accuracy: ",svcaccuracy)
                    print("svc F1: ", svcmarcof1)
                    all_svcLinear_accuracy.append(svcaccuracy)
                    all_svcLinear_f1.append(svcmarcof1)
                    counter+=1
        # write evaluation result to excel
        output = pd.DataFrame({'Author ':allname, "positive sample size":positive_sample_size,
                               "negative sample size":negative_sample_size, "Name group sample size": total_sample_size,
                                "logistic regression accuracy":all_LR_accuracy, "logistic regression f1": all_LR_f1,
                               "svc(linear) accuracy":all_svcLinear_accuracy, "svc(linear) f1": all_svcLinear_f1})
        savePath = "../../result/"+Dataset+"/binary_global_emb_sample=3m/"
        filename = "(Global emb sample 3m) textual="+select_emb+"_threshold="+str(step_threshold)+"_namegroupcount="+str(total_selected_group)+".csv"
        com_func.write_csv_df(savePath, filename, output)
        print("Done")
        
        threshold_change_all_lr_f1s.append(all_LR_f1)
        threshold_change_all_svm_f1s.append(all_svcLinear_f1)
        
    lr_diff_emb_f1_result.append(threshold_change_all_lr_f1s)
    svm_diff_emb_f1_result.append(threshold_change_all_lr_f1s)

Load embedding:  lsa
Total textual vector records: 3151504
Vector dimension:  100
For name:  j_read
j_read  pass
For name:  f_esteves
f_esteves  pass
For name:  c_miller
c_miller  pass
For name:  r_jha
r_jha  pass
For name:  a_lowe
a_lowe  pass
For name:  a_vega
a_vega  pass
For name:  k_smith
k_smith  pass
For name:  j_gordon
j_gordon  pass
For name:  s_liao
s_liao  pass
For name:  j_qian
j_qian  pass
For name:  s_bernardi
s_bernardi  pass
For name:  t_hill
t_hill  pass
For name:  s_schindler
s_schindler  pass
For name:  j_williams
j_williams  pass
For name:  s_jacobson
s_jacobson  pass
For name:  e_andrade
e_andrade  pass
For name:  t_santos
t_santos  pass
For name:  k_kim
Total sample size before apply threshold:  1111
Counter({'0000-0002-6929-5359': 211, '0000-0001-9498-284X': 154, '0000-0002-5878-8895': 139, '0000-0002-1864-3392': 92, '0000-0002-7045-8004': 57, '0000-0001-7896-6751': 57, '0000-0002-7991-9428': 55, '0000-0002-4010-1063': 45, '0000-0002-2186-3484': 28, '0000-0002-48

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

           0       0.00      0.00      0.00        45
           1       0.96      1.00      0.98       970

   micro avg       0.96      0.96      0.96      1015
   macro avg       0.48      0.50      0.49      1015
weighted avg       0.91      0.96      0.93      1015

[  0  45   0 970]
LR Accuracy:  0.9556650246305419
LR F1:  0.4886649874055416
              precision    recall  f1-score   support

           0       1.00      0.09      0.16        45
           1       0.96      1.00      0.98       970

   micro avg       0.96      0.96      0.96      1015
   macro avg       0.98      0.54      0.57      1015
weighted avg       0.96      0.96      0.94      1015

[  4  41   0 970]
svc Accuracy:  0.9596059113300492
svc F1:  0.5712843441263431
k_kim_1


/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

           0       0.00      0.00      0.00        57
           1       0.94      1.00      0.97       958

   micro avg       0.94      0.94      0.94      1015
   macro avg       0.47      0.50      0.49      1015
weighted avg       0.89      0.94      0.92      1015

[  0  57   0 958]
LR Accuracy:  0.9438423645320198
LR F1:  0.48555499239736444
              precision    recall  f1-score   support

           0       1.00      0.23      0.37        57
           1       0.96      1.00      0.98       958

   micro avg       0.96      0.96      0.96      1015
   macro avg       0.98      0.61      0.67      1015
weighted avg       0.96      0.96      0.94      1015

[ 13  44   0 958]
svc Accuracy:  0.9566502463054187
svc F1:  0.6744897959183673
k_kim_2


...

v_lopes  pass
For name:  m_quintana
m_quintana  pass
For name:  j_nunes
j_nunes  pass
For name:  z_nagy
z_nagy  pass
For name:  e_brown
e_brown  pass
For name:  j_nielsen
Total sample size before apply threshold:  913
Counter({'0000-0002-9955-6003': 487, '0000-0001-5568-2916': 105, '0000-0001-9414-1653': 104, '0000-0002-8747-6938': 57, '0000-0002-2831-7718': 39, '0000-0002-2854-8188': 35, '0000-0003-2228-5994': 24, '0000-0002-2058-3579': 23, '0000-0003-1730-3094': 13, '0000-0001-8521-7353': 9, '0000-0002-5211-948X': 8, '0000-0002-8112-8449': 6, '0000-0002-3418-4907': 2, '0000-0002-4760-3875': 1})
Total author before apply threshoid:  14
Total author after apply threshoid:  3
Total sample size after apply threshold:  696
Total missing sample:  0
(696, 100)
1
(696, 100)
j_nielsen_0
              precision    recall  f1-score   support

           0       0.99      0.99      0.99       487
           1       0.98      0.97      0.97       209

   micro avg       0.98      0.98      0.98  

j_kumar  pass
For name:  a_shenoy
a_shenoy  pass
For name:  h_yang
h_yang  pass
For name:  m_magnusson
m_magnusson  pass
For name:  m_foster
m_foster  pass
For name:  j_lynch
j_lynch  pass
For name:  j_boyle
j_boyle  pass
For name:  r_turner
r_turner  pass
For name:  s_brooks
s_brooks  pass
For name:  p_moreira
p_moreira  pass
For name:  s_mukhopadhyay
s_mukhopadhyay  pass
For name:  a_hudson
a_hudson  pass
For name:  d_thomas
d_thomas  pass
For name:  w_smith
w_smith  pass
For name:  l_martin
l_martin  pass
For name:  c_garcia
c_garcia  pass
For name:  g_huang
g_huang  pass
For name:  j_huber
j_huber  pass
For name:  j_qin
j_qin  pass
For name:  t_ho
t_ho  pass
For name:  c_keller
c_keller  pass
For name:  m_maia
m_maia  pass
For name:  p_bates
p_bates  pass
For name:  s_chow
s_chow  pass
For name:  m_simon
m_simon  pass
For name:  s_kar
s_kar  pass
For name:  d_vlachos
d_vlachos  pass
For name:  e_law
e_law  pass
For name:  m_ribeiro
m_ribeiro  pass
For name:  r_king
r_king  pass
For

Total missing sample:  0
(295, 100)
1
(295, 100)
w_wang_0
              precision    recall  f1-score   support

           0       0.98      0.95      0.96       101
           1       0.97      0.99      0.98       194

   micro avg       0.98      0.98      0.98       295
   macro avg       0.98      0.97      0.97       295
weighted avg       0.98      0.98      0.98       295

[ 96   5   2 192]
LR Accuracy:  0.976271186440678
LR F1:  0.9734606536518912
              precision    recall  f1-score   support

           0       0.98      0.89      0.93       101
           1       0.95      0.99      0.97       194

   micro avg       0.96      0.96      0.96       295
   macro avg       0.96      0.94      0.95       295
weighted avg       0.96      0.96      0.96       295

[ 90  11   2 192]
svc Accuracy:  0.9559322033898305
svc F1:  0.9499484475535428
w_wang_1
              precision    recall  f1-score   support

           0       0.97      0.99      0.98       194
           1 

t_o'brien  pass
For name:  s_may
s_may  pass
For name:  z_cai
z_cai  pass
For name:  a_pereira
a_pereira  pass
For name:  d_patel
d_patel  pass
For name:  a_james
a_james  pass
For name:  c_cao
c_cao  pass
For name:  c_brown
c_brown  pass
For name:  y_liang
y_liang  pass
For name:  y_fan
y_fan  pass
For name:  j_simon
j_simon  pass
For name:  m_jeong
m_jeong  pass
For name:  j_barrett
j_barrett  pass
For name:  d_elliott
d_elliott  pass
For name:  p_antunes
p_antunes  pass
For name:  x_yuan
x_yuan  pass
For name:  t_kim
t_kim  pass
For name:  a_cruz
a_cruz  pass
For name:  a_mora
a_mora  pass
For name:  j_walker
j_walker  pass
For name:  j_alves
j_alves  pass
For name:  j_seo
j_seo  pass
For name:  y_tang
y_tang  pass
For name:  a_norman
a_norman  pass
For name:  s_tanaka
s_tanaka  pass
For name:  c_wen
c_wen  pass
For name:  c_myers
c_myers  pass
For name:  v_santos
v_santos  pass
For name:  j_brown
j_brown  pass
For name:  b_pandey
b_pandey  pass
For name:  d_morgan
d_morgan  pass
Fo

Total missing sample:  0
(470, 100)
1
(470, 100)
j_kim_0
              precision    recall  f1-score   support

           0       0.97      0.92      0.94       124
           1       0.97      0.99      0.98       346

   micro avg       0.97      0.97      0.97       470
   macro avg       0.97      0.95      0.96       470
weighted avg       0.97      0.97      0.97       470

[114  10   4 342]
LR Accuracy:  0.9702127659574468
LR F1:  0.9610457268701602
              precision    recall  f1-score   support

           0       0.95      0.90      0.93       124
           1       0.97      0.98      0.97       346

   micro avg       0.96      0.96      0.96       470
   macro avg       0.96      0.94      0.95       470
weighted avg       0.96      0.96      0.96       470

[112  12   6 340]
svc Accuracy:  0.9617021276595744
svc F1:  0.949915934547349
j_kim_1
              precision    recall  f1-score   support

           0       0.97      0.95      0.96       146
           1   

In [ ]:
print(train_feature)
print(mnb_diff_feature_average_f1_result)
print(lr_diff_feature_average_f1_result)
print(svm_diff_freature_average_f1_result)
print(threshold_change)

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
threshold_change = np.array(threshold_change)
#--------------   logistic regression --------------------------#
# process result into np array
logistic_regression_result = np.array(combined_lr_result)
fig = plt.figure()
ax = plt.axes()
for emb_type, result in zip(combined_emb, logistic_regression_result):
    plt.plot(threshold_change, result, label=emb_type)
plt.legend()
plt.title('Average f1 for different feature in logistic regression')
plt.xlabel('Threshold')
plt.ylabel('marco f1 score')

# plt.savefig('diff_embedding_sample=3m_clf=logistic regression.eps', format='eps', dpi=300)


# -------------------- svm -------------------------------------#
svm_result = np.array(combined_svm_result)
fig = plt.figure()
ax = plt.axes()
for emb_type, result in zip(combined_emb, svm_result):
    plt.plot(threshold_change, result, label=emb_type)
plt.legend()
plt.title('Average f1 for different feature in SVM')
plt.xlabel('Threshold')
plt.ylabel('marco f1 score')

# plt.savefig('diff_embedding_sample=3m_clf=SVM.eps', format='eps', dpi=300)